In [13]:
import pandas as pd
import numpy as np
from pandas_datareader import data
import matplotlib.pyplot as plt
import seaborn as sns
from scipy import stats
import plotly.express as px
import math
import sys

import yfinance as yf
yf.pdr_override()

dataset = pd.read_csv('db/acoes1.csv')
dataset


Date   VALE3.SA  KEPL3.SA   VULC3.SA   LEVE3.SA   GGBR4.SA  \
0     2012-02-01  45.599998      2.00   8.000000  16.316666  16.571428   
1     2012-02-02  45.570000      2.00   8.000000  16.533333  16.809523   
2     2012-02-03  45.869999      2.00   7.440000  16.663334  17.295238   
3     2012-02-06  45.849998      2.00   7.440000  16.633333  17.333332   
4     2012-02-07  45.840000      2.00   7.440000  16.566666  17.428572   
...          ...        ...       ...        ...        ...        ...   
2907  2023-10-18  65.360001     10.44  18.540001  38.900002  21.660000   
2908  2023-10-19  64.419998     10.42  18.580000  38.759998  21.629999   
2909  2023-10-20  62.680000     10.46  18.290001  38.849998  21.450001   
2910  2023-10-23  62.560001     10.60  18.330000  38.000000  21.760000   
2911  2023-10-24  63.730000     10.56  18.309999  40.770000  21.639999   

       LREN3.SA   ALSO3.SA   DIRR3.SA   MILS3.SA  ...   CMIG4.SA  ITSA4.SA  \
0      9.630643  24.000000   9.970000  21.889999  ...  12.346126  5.575240   
1      9.799544  24.290001  10.050000  21.469999  ...  12.286963  5.594366   
2      9.975004  24.500000  10.100000  21.980000  ...  12.269552  5.608710   
3     10.002881  24.580000  10.170000  21.540001  ...  12.387913  5.618273   
4      9.873336  24.520000  10.170000  21.500000  ...  12.342644  5.675651   
...         ...        ...        ...        ...  ...        ...       ...   
2907  12.240000  21.990000  16.700001  10.600000  ...  11.680000  8.750000   
2908  12.340000  21.959999  16.750000  10.420000  ...  11.780000  8.800000   
2909  12.220000  22.020000  16.709999  10.600000  ...  11.810000  8.740000   
2910  12.400000  22.860001  17.049999  10.630000  ...  11.910000  8.730000   
2911  12.280000  23.120001  16.889999  10.740000  ...  11.930000  8.770000   

       BBAS3.SA   TASA4.SA   SLCE3.SA   B3SA3.SA   PETR4.SA   SUZB3.SA  \
0     27.480000  18.700001   6.921487   3.846666  24.950001  20.010000   
1     27.400000  18.920000   6.900826   3.893333  24.530001  20.010000   
2     27.299999  19.139999   6.892561   3.946666  24.610001  20.010000   
3     27.150000  19.030001   6.838842   3.946666  24.860001  20.010000   
4     27.250000  19.139999   6.979338   3.970000  25.600000  20.010000   
...         ...        ...        ...        ...        ...        ...   
2907  49.119999  15.480000  36.310001  11.130000  38.520000  56.080002   
2908  49.500000  15.470000  36.689999  11.000000  38.340000  55.980000   
2909  49.340000  15.340000  36.270000  11.150000  37.849998  54.900002   
2910  49.270000  15.770000  36.500000  11.310000  35.349998  54.400002   
2911  49.340000  15.770000  36.549999  11.560000  35.310001  52.049999   

      KLBN4.SA   BOVA11.SA  
0        1.596   63.520000  
1        1.552   63.590000  
2        1.552   64.209999  
3        1.532   64.190002  
4        1.550   64.949997  
...        ...         ...  
2907     4.660  110.370003  
2908     4.650  110.599998  
2909     4.550  109.500000  
2910     4.480  109.349998  
2911     4.420  109.820000  

[2912 rows x 24 columns]

In [14]:
def alocacao_ativos(dataset, dinheiro_total, seed = 0):
    if seed != 0:
        np.random.seed(seed)

    dataset = dataset.copy()
    
    pesos = np.random.random(len(dataset.columns)-1)
    pesos = pesos/ pesos.sum()
    colunas = dataset.columns[1:]

    for i in colunas:
        dataset[i] = dataset[i] / dataset[i][0]

    for i, acao in enumerate(dataset.columns[1:]):
        dataset[acao] = dataset[acao] * pesos[i] * dinheiro_total

    dataset['SOMA VALOR'] = dataset[colunas].sum(axis=1)

    datas = dataset['Date']

    dataset.drop(columns=['Date'], inplace=True)
    dataset['taxa de retorno'] = 0.0

    for i in range(1, len(dataset)):
        dataset['taxa de retorno'][i] = ((dataset['SOMA VALOR'][i] / dataset['SOMA VALOR'][i-1]) - 1 )*100

    acoes_pesos = pd.DataFrame(data= {'Ações': colunas, 'Pesos': pesos*100})

    return dataset, datas, acoes_pesos , dataset.loc[len(dataset)-1]['SOMA VALOR']

In [15]:
dataset, datas, acoes_pesos, soma_valor = alocacao_ativos(pd.read_csv('db/acoes1.csv'), 5000, 10)

In [16]:
figura = px.line(x = datas, y = dataset['taxa de retorno'], title=' Retorno diário')
figura.show()

In [17]:
figura = px.line(title=' Evolução patrimonio')

for i in dataset.drop(columns= [ 'SOMA VALOR', 'taxa de retorno']).columns:
    figura.add_scatter(x= datas, y = dataset[i], name = i)
figura.show()    

In [18]:
figura = px.line(x = datas, y = dataset['SOMA VALOR'], title=' Patrimônio')
figura.show()

In [19]:
dataset.loc[len(dataset)-1]['SOMA VALOR']/ dataset.loc[0]['SOMA VALOR'] -1 ## retorno acumulado

1.040580989426378

In [20]:
dataset['taxa de retorno'].std() ## desvio padrao

1.4434256994628354

In [21]:
# (dataset['taxa de retorno'].mean())/ dataset['taxa de retorno'].std() ## sharp ratio todo o periodo 
(dataset['taxa de retorno'].mean())/ dataset['taxa de retorno'].std() * math.sqrt(246) ## sharp ratio anual 

0.38024064954793274

In [22]:
dinheiro_total = 5000
soma_valor - dinheiro_total

5202.90494713189

In [23]:
taxa_selic_2020 = 12
taxa_selic_2021 = 13.75
taxa_selic_2022 = 13.75
taxa_selic_2023 = 13.25
valor_2020 = dinheiro_total + (dinheiro_total * taxa_selic_2020 / 100)
valor_2021 = valor_2020 + (dinheiro_total * taxa_selic_2021 / 100)
valor_2022 = valor_2021 + (dinheiro_total * taxa_selic_2022 / 100)
valor_2023 = valor_2022 + (dinheiro_total * taxa_selic_2023 / 100)
valor_2023


7637.5

In [24]:
taxa_selic_historico = np.array([taxa_selic_2020, taxa_selic_2021, taxa_selic_2022, taxa_selic_2023])

(dataset['taxa de retorno'].mean() - taxa_selic_historico.mean()/100)/ dataset['taxa de retorno'].std() * math.sqrt(246) #sharp ratio validando historico da selic

-1.0527243828997648

In [25]:
dataset

VALE3.SA   KEPL3.SA    VULC3.SA    LEVE3.SA    GGBR4.SA    LREN3.SA  \
0     338.359379   9.103369  277.965883  328.481831  218.682755   98.612755   
1     338.136784   9.103369  277.965883  332.843704  221.824737  100.342217   
2     340.362827   9.103369  258.508273  335.460844  228.234425  102.138835   
3     340.214420   9.103369  258.508273  334.856880  228.737122  102.424279   
4     340.140231   9.103369  258.508273  333.514750  229.993939  101.097804   
...          ...        ...         ...         ...         ...         ...   
2907  484.981798  47.519586  644.185965  783.122238  285.833445  125.331207   
2908  478.006827  47.428555  645.575760  780.303739  285.437545  126.355159   
2909  465.095761  47.610622  635.499531  782.115593  283.062219  125.126422   
2910  464.205350  48.247859  636.889326  765.003699  287.153088  126.969522   
2911  472.886926  48.065792  636.194396  820.768451  285.569512  125.740786   

       ALSO3.SA    DIRR3.SA   MILS3.SA    RANI3.SA  ...    BBAS3.SA  \
0     86.885303  333.626102  74.184761   38.752502  ...  268.700108   
1     87.935171  336.303140  72.761389   38.752502  ...  267.917866   
2     88.695414  337.976296  74.489770   38.752502  ...  266.940060   
3     88.985031  340.318696  72.998623   38.752502  ...  265.473360   
4     88.767820  340.318696  72.863061   38.752502  ...  266.451166   
...         ...         ...        ...         ...  ...         ...   
2907  79.608658  558.832098  35.923185  422.650434  ...  480.296551   
2908  79.500049  560.505222  35.313168  427.613813  ...  484.012211   
2909  79.717267  559.166671  35.923185  432.195385  ...  482.447728   
2910  82.758254  570.544096  36.024853  435.249767  ...  481.763270   
2911  83.699512  565.190021  36.397640  429.141004  ...  482.447728   

        TASA4.SA    SLCE3.SA     B3SA3.SA    PETR4.SA    SUZB3.SA    KLBN4.SA  \
0     316.616291  128.038846   402.604916  313.466806  238.000859   62.366500   
1     320.341177  127.656646   407.489225  308.190010  238.000859   60.647126   
2     324.066063  127.503753   413.071240  309.195113  238.000859   60.647126   
3     322.203636  126.510018   413.071240  312.336062  238.000859   59.865587   
4     324.066063  129.109023   415.513457  321.633271  238.000859   60.568969   
...          ...         ...          ...         ...         ...         ...   
2907  262.097318  671.689593  1164.902969  483.957561  667.020912  182.097675   
2908  261.928016  678.719066  1151.296723  481.696073  665.831476  181.706917   
2909  259.726939  670.949626  1166.996184  475.539791  652.985876  177.799245   
2910  267.007425  675.204329  1183.742402  444.130292  647.038828  175.063866   
2911  267.007425  676.129253  1209.908236  443.627776  619.087676  172.719263   

       BOVA11.SA    SOMA VALOR  taxa de retorno  
0     163.775401   5000.000000         0.000000  
1     163.955883   5011.141850         0.222837  
2     165.554444   5016.476411         0.106454  
3     165.502886   5018.397799         0.038302  
4     167.462401   5040.196511         0.434376  
...          ...           ...              ...  
2907  284.570078  10181.697594        -1.488439  
2908  285.163083  10177.602050        -0.040225  
2909  282.326926  10131.452621        -0.453441  
2910  281.940172  10125.285362        -0.060872  
2911  283.151990  10202.904947         0.766592  

[2912 rows x 25 columns]

In [26]:
def alocacao_portfolio(dataset, dinheiro_total, sem_risco, repeticoes):
  dataset = dataset.copy()
  dataset_original = dataset.copy()

  lista_retorno_esperado = []
  lista_volatilidade_esperada = []
  lista_sharpe_ratio = []

  melhor_sharpe_ratio = 1 - sys.maxsize
  melhores_pesos = np.empty
  melhor_volatilidade = 0
  melhor_retorno = 0
  
  for _ in range(repeticoes):
    pesos = np.random.random(len(dataset.columns) - 1)
    pesos = pesos / pesos.sum()

    for i in dataset.columns[1:]:
      dataset[i] = dataset[i] / dataset[i][0]

    for i, acao in enumerate(dataset.columns[1:]):
      dataset[acao] = dataset[acao] * pesos[i] * dinheiro_total

    dataset.drop(labels = ['Date'], axis = 1, inplace=True)

    retorno_carteira = np.log(dataset / dataset.shift(1))
    matriz_covariancia = retorno_carteira.cov()

    dataset['soma valor'] = dataset.sum(axis = 1)
    dataset['taxa retorno'] = 0.0

    for i in range(1, len(dataset)):
      dataset['taxa retorno'][i] = np.log(dataset['soma valor'][i] / dataset['soma valor'][i - 1])

    #sharpe_ratio = (dataset['taxa retorno'].mean() - sem_risco) / dataset['taxa retorno'].std() * np.sqrt(246)
    retorno_esperado = np.sum(dataset['taxa retorno'].mean() * pesos) * 246
    volatilidade_esperada = np.sqrt(np.dot(pesos, np.dot(matriz_covariancia * 246, pesos)))
    sharpe_ratio = (retorno_esperado - sem_risco) / volatilidade_esperada

    if sharpe_ratio > melhor_sharpe_ratio:
      melhor_sharpe_ratio = sharpe_ratio
      melhores_pesos = pesos
      melhor_volatilidade = volatilidade_esperada
      melhor_retorno = retorno_esperado

    lista_retorno_esperado.append(retorno_esperado)
    lista_volatilidade_esperada.append(volatilidade_esperada)
    lista_sharpe_ratio.append(sharpe_ratio)
    
    dataset = dataset_original.copy()

  return melhor_sharpe_ratio, melhores_pesos, lista_retorno_esperado, lista_volatilidade_esperada, lista_sharpe_ratio, melhor_volatilidade, melhor_retorno

In [27]:
melhor_sharpe_ratio, melhores_pesos = alocacao_portifolio(pd.read_csv('db/acoes1.csv'), 5000, taxa_selic_historico.mean()/100, 100)

NameError: name 'alocacao_portifolio' is not defined